# State-space analysis

We illustrate state-space analysis with `ecco` using the same termites model as for static analysis.

## Loading the model

First, we load the model and construct a component graph from it by calling `model` object as a function.

In [1]:
%run -m ecco rr-termites.rr
g0 = model()

`g0` is an instance of class `ComponentGraph` that is the main class we deal with when performing state-space analysis. A component graph is a collection of components (pairwise disjoint sets of states), linked by the transitions allowing to reach one component from another. These transitions are applications of the actions defined in the MRR model. A component graph is handled by:

 - splitting (some of) its component wrt properties
 - merging or dropping some components
 - checking properties onto (some of) its components
 - drawing it to explore its information

To illustrate, we start by splitting `g0` into its initial states, deadlocks, and strongly connected components (SCC), plus the remaining states that do not fall into any of these categories. This split will be explained more in detail later on. Then we draw the resulting component graph (to do so, we just let `g1` be the result of the Python cell, which results in displaying it as an interactive graph).

In [2]:
g1 = g0.split(INIT, DEAD, SCC)
g1

In the drawing above, we can recognise:

 - the initial states marked by ▶
 - strongly connected components (SCC) marked by ⏺
 - deadlocks marked by ⏹

This will be detailed later on.

`ComponentGraph` is equipped with the standard Python interface for containers, for instance with `g1`:

 - `g1[num]` returns the component whose number is `num`
 - `g1|src,dst]` returns the annotation of an edge from component `num` to `dst`
 - `len(g1)` returns the number of components it holds, here 7
 - finally, `g1` may be iterated over, yielding its components

More specifically, every instance is equipped with two tables:

 - `g1.nodes` gathers all the information about components
 - `g1.edges` gathers all the information about the edges linking components

In [3]:
g1.nodes

size                                         consts  \
node                                                        
1        2  (Ai-, Ec-, Fg-, Md-, Rp+, Sd-, Te-, Wd-, Wk-)   
3        6                 (Ec-, Fg-, Rp-, Sd-, Te-, Wk-)   
5        2  (Ac-, Ai-, Ec+, Fg-, Md-, Rp+, Sd-, Te-, Wd-)   
6        2  (Ac+, Ai-, Ec+, Fg-, Md-, Rp+, Sd-, Te-, Wd-)   
7       20                           (Ac-, Ec+, Md+, Rp+)   
8       20                           (Ac+, Ec+, Md+, Rp+)   
9       62                                     (Rp-, Wk-)   

                              HASNO HAS CONTAINS    ISIN       EQUALS  
node                                                                   
1           (DEAD, HULL, hull, scc)  ()       ()      ()       (INIT)  
3           (HULL, INIT, hull, scc)  ()       ()      ()       (DEAD)  
5                      (DEAD, INIT)  ()       ()  (HULL)  (hull, scc)  
6                      (DEAD, INIT)  ()       ()  (HULL)  (hull, scc)  
7                      (DEAD, INIT)  ()       ()  (HULL)  (hull, scc)  
8                      (DEAD, INIT)  ()       ()  (HULL)  (hull, scc)  
9     (DEAD, HULL, INIT, hull, scc)  ()       ()      ()           ()

`g1` has 7 components numbered 1, 3, 5, 6, 7, 8, 9. Component numbers are chosen sequentially as components are constructed, and they are identifiers in the sense that if two components have the same number, then we are sure they hold exactly the same set of states, even if they have been constructed in different ways. The nodes table has several columns:

 - _size_ gives the number of states contained by each component
 - _consts_ is the set of variables valuation that remain constant over all the states of each component, for instance in component 9, `Rp` and `Wk` are always off
 - the remaining columns list the relation of the components, considered as a set of states, with the properties checked on it. Here we see only _topological properties_ that are automatically checked on every component when it is first created:
   - `INIT` is the set of all the initial states of the model
   - `DEAD` is the set of all states that are deadlocks (ie, states from which no transition is possible)
   - `HULL` is the set of all the states that form the convex hull of the strongly connected components (SCC)
   - `hull` is the set of all states that form an SCC hull within the component, contrasting with `HULL` that considers the whole set of reachable states
   - `scc` is any SCC within a component

   Each column describes the relation between each component and some properties:
   - having `p` in _HASNO_ means that the component has no states that validate `p`, for instance, component 1 has no deadlocks
   - having `p` in _HAS_ means that the component has some states that validate `p`, but not all of them
   - having `p` in _CONTAINS_ means that the component contains all the states that validate `p`, but it has other states that do not
   - having `p` in _ISIN_ means that the component is entirely contained in the states that validate `p`, but other states that do are not in the component, for instance, component 5 is fully contained within the SCC hull
   - having `p` in _EQUALS_ means that the component holds exactly all the states that validate `p`, for instance, component 5 is itself an SCC hull and also an SCC (de facto, any SCC is also a convex hull)

As we check more properties on a component graph, or split it wrt properties, we will populate the nodes tables with more properties.

In [4]:
g1.edges

actions                      tags
src dst                                            
1   3          (R11, R12)              (depl, depl)
    5                (R4)                    (prod)
    6                (R4)                    (prod)
5   7                (R2)                    (prod)
    9               (R12)                    (depl)
6   8                (R2)                    (prod)
    9          (R11, R12)              (depl, depl)
7   9               (R12)                    (depl)
8   7               (R10)                    (cons)
    9          (R11, R12)              (depl, depl)
9   3    (C1, R7, R8, R9)  (depl, depl, depl, prod)

The edges table is currently empty. It is indexed by the source and destination component numbers, and has two columns:

 - `actions` is the set of actions that correspond to this edge
 - `tags` is the set of tags associated to these actions

Note that the nodes and edges tables can be explored from the drawing of a component graph by opening the _Inspector_ tab and clicking on nodes to select or unselect them.

## Properties

Before going further into state-space analysis, we need to describe the properties that can be checked on components, or used to split them.

### Topological properties

These are the properties we have observed in `g1` above, plus others:

 - `INIT`, `DEAD`, and `HULL`, as described above
 - `ENTRY` is the set of states through which a component may be entered, that is, the states reached by a transition coming from another component
 - `EXIT` is the set of states from which a component may be exited, that is, the states from which a transition can lead to another component
 - `SCC` is a set of at least two states forming a maximal strongly connected component, we have used this property to split `g0`

All these properties are gathered into an enumerated type `topo`, and we can use, eg, `topo.INIT` or `INIT` that are the same value.

### (AR)CTL properties

CTL (Computation Tree Logic) is a temporal logic that allows to characterise states with respect to what happens or not in the states that are reachable in the future. A formula can be seen as a statement about a state `s`, that is validated by exploring the states reachable from `s`. CTL formulas have to respect the following syntax:

 - atoms are variable names or valuation, they may be quoted as in `"AG"` or `'EX'` to avoid conflicts with reserved keywords of CTL, such a formula is true on every state where the variable has the given value, for instance:
   - `Rp` is true where `Rp` is on
   - `Rp+` is the same, just more explicit
   - `Rp==1` is the same again, even more explicit
   - `Rp-` or `Rp==0` are true where `Rp` is off
   - if a variable has a long name with dots are square brackets, the atom must be quoted, eg `"nest[0].inside"` and `"nest[0].inside==2"` are valid atoms; note how quotes must be around the whole atom, not only the variable name
   - comparisons are not limited to `==` but may be also `!=` (not equal), `<`, `<=`, `>`, or `>=` with the usual meanings
 - sub-formulas may be enclosed into parentheses to force operators priority
 - Boolean operators can be used to combine sub-formulas:
   - `~form` (NOT) is a formula that holds on states where `form` does not
   - `left & right` (AND) holds on states where both `left` and `right` sub-formulas do
   - `left | right` (OR) holds on states where either `left` or `right` sub-formulas do, possibly both
   - `left => right` (IMPLY) holds on states where when `left` holds then `right` has to hold also, this is actually a shorthand for `~left | right`
   - `left <=> right` (IFF) is a shorthand for `(left => right) & (right => left)`
 - modalities allow to express conditions with respect to the future of states: `X` (NEXT), `F` (FUTURE), `G` (GLOBALLY), `U` (UNTIL), and `R` (RELEASE). Each modality must be quantified by either `A` (ALWAYS), or `E` (EXISTS). So a formula may be either:
   - `A path` holds on a state `s` if `path` does on all paths starting from `s`
   - `E path` holds on a state `s` if `path` does on one path starting from `s`
   
   `path` must then be a path formula, that is one formula qualified with a unary modality of two formulas connected by a binary modality:
   * `X form` holds if `form` holds on the next state
   * `F form` holds if `form` holds eventually in the future
   * `G form` holds if `form` holds from now on and forever
   * `left U right` holds if `left` holds until `right` holds forever
   * `left R right` holds if `right` holds until a state where `left` holds is reached, but then `left` or `right` are not required to hold anymore

CTL formulas can be constructed from patterns representing typical queries, see the [CTL wizard](https://www.ibisc.univ-evry.fr/~fpommereau/wiz/).

ARCTL is a variant of CTL where quantifiers apply to a subset of actions. For instance `A{a|b}X Sd` is like `AX Sd` but only considering actions tagged by `a` or `b`. Tags are specified in the MRR model at the beginning of actions, for instance in `[one,two] Rp+ >> Ec+`, `one` and `two` are two such tags.

More information about CTL and ARCTL can be found in [DOI:10.1371/journal.pcbi.1009657](https://doi.org/10.1371/journal.pcbi.1009657).

### `ecco` states properties

`ecco` also comes with its own syntax to define properties. This allows to build simple expressions that correspond to sets of states. Atoms are:

 - `DEAD`, `INIT`, and `HULL`, corresponding to the topological properties as presented above
 - `ALL` corresponding to the set of all reachable states
 - `Cx` where `x` is a component number, corresponding to the set of this particular component

These base sets of states can then be combined with the usual Python sets operations: `|` for the union, `&` for the intersection, and `-` for the difference. Moreover, various functions allow to compute new sets from existing ones:

 - `hull(s)` is the convex hull of the SCCs included in a set of states `s`
 - `past(s)` is all the states that allow to reach `s`, including `s` itself
 - `basin(s)` is the set of states from which reaching `s` cannot be avoided, which includes `s` but excludes states in SCCs for instance (as reaching `s` may be avoided by looping within an SCC)
 - `pick(s)` is one arbitrary state chosen in `s`
 - `succ(s)` is the set of states of successors states of `s`, which is the states reachable from `s` through one transition
 - `succ_s(s)` is the transitive closure of `succ|id`, which is all the states in `s` or reachable from it
 - `succ_o(s)` is the transitive closure of `succ&id`, which is the subset of `s` that remains stable through `succ`
 - `pred(s)`, `pred_s(s)`, and `pred_o(s)` are like `succ(s)`, `succ_s(s)` and `succ_o(s)` but considering the predecessor relation instead of the successor relation
 - `entries(s)` is the subset of `s` that can be reached from its outside through one transition
 - `exists(s)` is the subset of `s` that allows to reach its outside through one transition
 - `oneway(a, s)`, where `a` is an action is the subset of `s` that can be reached through action `a` in an irreversible transition, that is, when `a` is fired from a given state, this state is not reachable anymore after firing `a`

In all these functions, `s` may be omitted in which case, the states of the component on which the formula is evaluated are used instead of `s`. Additionally to the functions above, given an action `a`, others are available:

 - `LTS.succ[a]` is the successor function through `a`
 - similarly `LTS.pred[a]` is the predecessor function through `a`
 - `LTS.enable(a)` is the set of states from which `a` can be fired

## Managing components

### Splitting 

Using properties, we can split components as we did above. `g0.split(INIT, DEAD, SCC)` requests the splitting of all the components of `g0` wrt three topological properties. First, it splits apart the states that belong to `INIT` and those that do not. Then the resulting components are split again wrt `DEAD`. Finally, the result is again split against `SCC` which will split apart every SCC in every component.

In general, method `split()` expects first a series of properties:

 - topological properties specified as values `INIT`, `DEAD`, etc.
 - (AR)CTL properties specified as strings
 - `ecco` state formulas are also specified as strings

Then, `split()` expects a series of component numbers, but if none is given like above, all the components are considered for splitting. It performs the splits in the order of its arguments and returns a new component graph. `split()` also accepts keyword arguments to hide complex formulas in the nodes table:

In [5]:
g0.split(must_die="basin(DEAD)").nodes

size      consts                    HASNO HAS                 CONTAINS  \
node                                                                           
10      68  (Rp-, Wk-)  (HULL, INIT, hull, scc)  ()                   (DEAD)   
11      46       (Rp+)         (DEAD, must_die)  ()  (HULL, INIT, hull, scc)   

     ISIN      EQUALS  
node                   
10     ()  (must_die)  
11     ()          ()

Here we split `g0` and directly display the nodes table of the resulting component graph. In this table we see that formula `"attractor(DEAD)"` is displayed as `must_die` as we passed it using this keyword argument.

Method `split()` accepts two options:

 - `_warn=True` can be set to `False` in order to suppress the warning issued when a property is found to match no states
 - `_limit=256` causes splitting to pause when it results in a component graph with more that 256 states, asking user if it should continue or not (answering yes will continue the splitting but ask again the question every new 256 components). Setting `_limit=0` will disable interaction forcing the full split even if it leads to a huge number of components

### Merging

Another method is `merge()`, it expects a series of component numbers and return a component graph where they have been merged into a unique component. For instance:

In [6]:
g1.merge(5, 6, 7, 8)

The merged component yielded new component 12, with a new icon on it. These icons will be described below.

### Dropping

Another method is `drop()`. It works like `merge()` but completely removes the given components instead of merging them:

In [7]:
g1.drop(5, 6, 7, 8)

### Expliciting

The last method related to managing the components is `explicit()`. It expects a series of component numbers and splits them into their individual states. If no component is given, then all are explicited. Like `split()`, it has an option `_limit` to avoid accidentally building huge component graphs.

In [8]:
x = g1.explicit()
x.nodes

size                                              consts  \
node                                                             
13       1  (Ac-, Ai-, Ec-, Fg-, Md-, Rp+, Sd-, Te-, Wd-, Wk-)   
14       1  (Ac+, Ai-, Ec-, Fg-, Md-, Rp+, Sd-, Te-, Wd-, Wk-)   
15       1  (Ac-, Ai-, Ec-, Fg-, Md-, Rp-, Sd-, Te-, Wd-, Wk-)   
16       1  (Ac+, Ai-, Ec-, Fg-, Md-, Rp-, Sd-, Te-, Wd-, Wk-)   
17       1  (Ac-, Ai+, Ec-, Fg-, Md+, Rp-, Sd-, Te-, Wd-, Wk-)   
...    ...                                                 ...   
122      1  (Ac+, Ai+, Ec-, Fg+, Md+, Rp-, Sd+, Te-, Wd+, Wk-)   
123      1  (Ac-, Ai-, Ec+, Fg+, Md+, Rp-, Sd+, Te-, Wd+, Wk-)   
124      1  (Ac+, Ai-, Ec+, Fg+, Md+, Rp-, Sd+, Te-, Wd+, Wk-)   
125      1  (Ac-, Ai+, Ec+, Fg+, Md+, Rp-, Sd+, Te-, Wd+, Wk-)   
126      1  (Ac+, Ai+, Ec+, Fg+, Md+, Rp-, Sd+, Te-, Wd+, Wk-)   

                              HASNO HAS CONTAINS    ISIN EQUALS  component  
node                                                                        
13          (DEAD, HULL, hull, scc)  ()       ()  (INIT)     ()          1  
14          (DEAD, HULL, hull, scc)  ()       ()  (INIT)     ()          1  
15          (HULL, INIT, hull, scc)  ()       ()  (DEAD)     ()          3  
16          (HULL, INIT, hull, scc)  ()       ()  (DEAD)     ()          3  
17          (HULL, INIT, hull, scc)  ()       ()  (DEAD)     ()          3  
...                             ...  ..      ...     ...    ...        ...  
122   (DEAD, HULL, INIT, hull, scc)  ()       ()      ()     ()          9  
123   (DEAD, HULL, INIT, hull, scc)  ()       ()      ()     ()          9  
124   (DEAD, HULL, INIT, hull, scc)  ()       ()      ()     ()          9  
125   (DEAD, HULL, INIT, hull, scc)  ()       ()      ()     ()          9  
126   (DEAD, HULL, INIT, hull, scc)  ()       ()      ()     ()          9  

[114 rows x 8 columns]

The nodes table has 126 rows, which corresponds to every reachable state of the model we are analysing. Note how a column _component_ has been added to keep track of which component every state comes from.

## Managing properties

### Checking properties

Method `check()` has the same interface as `split()` (except for `_limit`), but instead of splitting components, it only checks properties onto their sets of states, adding the result to the nodes table. When checking properties on a given component graph `g`, only the nodes table of `g` is updated. If another component graph `h` shares components with `g`, the properties checked on `g` will not be visible in the nodes tables of `h`. To have them, it is necessary to call method `h.update()`.

### Removing properties

Method `forget()` has the same interface as `check()`, but instead of checking new properties, it forgets about properties already checked. Forgot properties are removed from the components and from the nodes table. Method `forget_all()` expects only component numbers and forgets about all the properties already checked.

### Tagging components

Method `tag()` expects at least one string and a series of component numbers (if none is given, it will consider all the components) and creates for each component a dummy property named after the passed string. This property does not need to follow any particular syntax, it is just an arbitrary string that is made to correspond with the states of the component. If several components are passed, the state corresponding to the tag will be the union of the components' states.

## Managing nodes and edges tables

A component graph, eg `g1`, has two more attributes related to the nodes and edges tables:

 - `g1.n` is related to `g1.nodes`
 - `g1.e` is related to `g1.edges`

Both can be displayed to have a summary of the corresponding table, for instance:

In [9]:
g1.n

size                                         consts  \
count         7.0                                              7   
unique                                                         7   
top                (Ai-, Ec-, Fg-, Md-, Rp+, Sd-, Te-, Wd-, Wk-)   
freq                                                           1   
mean    16.285714                                                  
std     21.738708                                                  
min           2.0                                                  
25%           2.0                                                  
50%           6.0                                                  
75%          20.0                                                  
max          62.0                                                  

               HASNO HAS CONTAINS    ISIN       EQUALS  
count              7   7        7       7            7  
unique             4   1        1       2            4  
top     (DEAD, INIT)  ()       ()  (HULL)  (hull, scc)  
freq               4   7        7       4            4  
mean                                                    
std                                                     
min                                                     
25%                                                     
50%                                                     
75%                                                     
max

This is equivalent to calling `g1.nodes.describe(include="all")`. See [pandas documentation](https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.describe.html) for more details.

Additionally, deleting items in `g1.n` will delete the corresponding columns in `g1.nodes`, and assigning items will create a new column. For example, assume we want a column in the nodes table that gives the number of constants in each component. First, let's display the nodes table:

In [10]:
g1.nodes

size                                         consts  \
node                                                        
1        2  (Ai-, Ec-, Fg-, Md-, Rp+, Sd-, Te-, Wd-, Wk-)   
3        6                 (Ec-, Fg-, Rp-, Sd-, Te-, Wk-)   
5        2  (Ac-, Ai-, Ec+, Fg-, Md-, Rp+, Sd-, Te-, Wd-)   
6        2  (Ac+, Ai-, Ec+, Fg-, Md-, Rp+, Sd-, Te-, Wd-)   
7       20                           (Ac-, Ec+, Md+, Rp+)   
8       20                           (Ac+, Ec+, Md+, Rp+)   
9       62                                     (Rp-, Wk-)   

                              HASNO HAS CONTAINS    ISIN       EQUALS  
node                                                                   
1           (DEAD, HULL, hull, scc)  ()       ()      ()       (INIT)  
3           (HULL, INIT, hull, scc)  ()       ()      ()       (DEAD)  
5                      (DEAD, INIT)  ()       ()  (HULL)  (hull, scc)  
6                      (DEAD, INIT)  ()       ()  (HULL)  (hull, scc)  
7                      (DEAD, INIT)  ()       ()  (HULL)  (hull, scc)  
8                      (DEAD, INIT)  ()       ()  (HULL)  (hull, scc)  
9     (DEAD, HULL, INIT, hull, scc)  ()       ()      ()           ()

Then, we need to create a function that will take a row of the nodes table and return the value we want to put in the new column for this row. Here, we just take `row.consts`, which is the content of column `consts` for the given `row`, and return its length.

In [11]:
def const_count(row):
    return len(row.consts)

g1.n["coco"] = const_count
g1.nodes

size                                         consts  \
node                                                        
1        2  (Ai-, Ec-, Fg-, Md-, Rp+, Sd-, Te-, Wd-, Wk-)   
3        6                 (Ec-, Fg-, Rp-, Sd-, Te-, Wk-)   
5        2  (Ac-, Ai-, Ec+, Fg-, Md-, Rp+, Sd-, Te-, Wd-)   
6        2  (Ac+, Ai-, Ec+, Fg-, Md-, Rp+, Sd-, Te-, Wd-)   
7       20                           (Ac-, Ec+, Md+, Rp+)   
8       20                           (Ac+, Ec+, Md+, Rp+)   
9       62                                     (Rp-, Wk-)   

                              HASNO HAS CONTAINS    ISIN       EQUALS  coco  
node                                                                         
1           (DEAD, HULL, hull, scc)  ()       ()      ()       (INIT)     9  
3           (HULL, INIT, hull, scc)  ()       ()      ()       (DEAD)     6  
5                      (DEAD, INIT)  ()       ()  (HULL)  (hull, scc)     9  
6                      (DEAD, INIT)  ()       ()  (HULL)  (hull, scc)     9  
7                      (DEAD, INIT)  ()       ()  (HULL)  (hull, scc)     4  
8                      (DEAD, INIT)  ()       ()  (HULL)  (hull, scc)     4  
9     (DEAD, HULL, INIT, hull, scc)  ()       ()      ()           ()     2

Essentially, the function we assign to `g1.n[...]` is called repeatedly being passed each row of the nodes table. Rows are passed as `pandas.Series` objects indexed by the column names and having an attribute `.node` that corresponds to the index of the row (ie, the node number). Then, the values returned by each call are accumulated to form the content of the new column that is added to the nodes table. This is similar to the calling of method `pandas.DataFrame.apply`. Column _size_ of a nodes table contains integers while the other columns contain instances of a class `hset` that is similar to `set` but displays its elements sorted.

Attribute `.e` works exactly as `.n` but with the edges table.

## Querying component graphs

### Finding components by properties

Earlier, we used `g1.merge(5, 6, 7, 8)` to merge all the components that were SCCs, but it was quite tedious and error-prone to search for ⏺ marks in the graph and report the component numbers. In general, it may not be possible to rely on the graphical representation, either because it is not readable, or because there are no marks for the property we are interested in. As a solution to this, a component graph has a query interface allowing one to search components by their properties. For instance, we could have used:

In [12]:
g1.merge(*g1.EQUALS("scc"))

Here, `g1.EQUALS("scc")` returns all the component numbers that have property `"scc"` in their column _EQUALS_, adding `*` before tells Python that we want to pass each of these numbers as a single argument to `merge()`. More generally, a component graph has methods corresponding to each of its columns _HASNO_ to _EQUALS_. It also has methods with the relation spelt in lower case, eg, `g1.equals(...)` instead of `g1.EQUALS(...)` the difference between the lower- and upper-case version is that the latter is strict and the former is relaxed. Strict relation means that the property has to appear exactly in the given column, while relaxed relation means that the property is interpreted in more general terms, for instance, `g1.has(p)` will search `p` in column _HAS_, but also in _CONTAINS_, _ISIN_, or _EQUALS_ because if a component is in `p`, it also has states from `p`. These relaxed interpretations are listed below:

| relaxed relation | searched columns                    |
|:-----------------|:------------------------------------|
| `hasno`          | `HASNO`                             |
| `has`            | `HAS`, `CONTAINS`, `ISIN`, `EQUALS` |
| `contains`       | `CONTAINS`, `EQUALS`                |
| `isin`           | `ISIN`, `EQUALS`                    |
| `equals`         | `EQUALS`                            |

So far, the queries we have seen only work for topological properties. A more general way to search for any property is to call the component graph as a function. For instance, instead of `g1.equals("scc")`, we could have used `g1("scc", EQUALS, strict=False)` where:

 - `"scc"` is the property searched for
 - `EQUALS` is the relation we want to match
 - `strict=False` requests a relaxed match instead of a strict match (`strict=` could have been omitted)

This will work for any relations, including (AR)CTL or `ecco` states properties passed as strings, or even aliases as `must_die` as we have used above. The value returned by such a call (or the shorthands we started the presentation with) is a set of component numbers and we can combine several queries using the usual Python set operations: `|` union, `&` intersection, `-` difference, and even `~` complement.

A more high-level search is provided by the method `select()` that takes a series of properties and an option `_all`:

 - if `_all=True`, it returns the component numbers that match all of the passed properties
 - if `_all=False`, it returns the component numbers that match any of the passed properties

Additionally to searching, method `select()` also calls `check()` if the properties have not been checked already. This contrasts with the previous queries that will never find a property that was not checked before.

### Statistical queries

A component graph also has a method `count()` to count the number of times each variables appears in each value in the states stored in its components, for instance:

In [13]:
g1.count()

1  3  5  6   7   8   9
variable value                        
Ac       0      1  3  2  0  20   0  23
         1      1  3  0  2   0  20  39
Ai       0      2  2  2  2  10  10  34
         1      0  4  0  0  10  10  28
Ec       0      2  6  0  0   0   0  28
         1      0  0  2  2  20  20  34
Fg       0      2  6  2  2   4   4  22
         1      0  0  0  0  16  16  40
Md       0      2  2  2  2   0   0   2
         1      0  4  0  0  20  20  60
Rp       0      0  6  0  0   0   0  62
         1      2  0  2  2  20  20   0
Sd       0      2  6  2  2  12  12  46
         1      0  0  0  0   8   8  16
Te       0      2  6  2  2  12  12  46
         1      0  0  0  0   8   8  16
Wd       0      2  4  2  2  16  16  32
         1      0  2  0  0   4   4  30
Wk       0      2  6  1  1   6   6  62
         1      0  0  1  1  14  14   0

Here, we see on the first line that `Ac` appear with value 0:

 - 1 time in component 1
 - 3 times in component 3
 - 2 times in component 5
 - etc.

Using method `pca()` a principal component analysis is performed on the matrix returned by `count()`:

In [14]:
g1.pca()

component              0         1
variable value                    
Ac       0     -0.056424 -0.189769
         1      0.056424  0.189769
Ai       0     -1.697602 -0.038794
         1      1.697602  0.038794
Ec       0      0.814063  2.505931
         1     -0.814063 -2.505931
Fg       0     -1.786317  1.563543
         1      1.786317 -1.563543
Md       0     -1.525710  0.817101
         1      1.525710 -0.817101
Rp       0      2.104701  2.492432
         1     -2.104701 -2.492432
Sd       0     -1.932321  0.851818
         1      1.932321 -0.851818
Te       0     -1.932321  0.851818
         1      1.932321 -0.851818
Wd       0     -2.028266 -0.426568
         1      2.028266  0.426568
Wk       0     -0.426464  2.100887
         1      0.426464 -2.100887

## High-level operations on component graphs

### Classifying the components

Method `classify()` performs a series of splits with respect to properties all passed as keywords in order to separate states that satisfy or not each property. These properties are considered as classes and a column can be added to the nodes table to list to which class each component of the resultin graph belongs to. For instance, assuming we want to analyse our model wrt to deadlocks. There may exist three situations:

 - the system has reached a deadlock or is forced to eventually reach one, this corresponds to `ecco` state formula `"attractor(DEAD)"`
 - the system may reach a deadlock, but not necessarily, this corresponds to the formula `"basin(DEAD)"`
 - the system can loop into SCC infinitely in order to avoid reaching a deadlock, this corresponds to the formula `"HULL"`

We can classify the states of `g0` using these three properties, writing a summary in column _class_ as follows:

In [15]:
c = g0.classify(must_lock="basin(DEAD)", waiting="HULL", may_lock="past(DEAD)", _col="class")
c.nodes

size                                         consts  \
node                                                        
1        2  (Ai-, Ec-, Fg-, Md-, Rp+, Sd-, Te-, Wd-, Wk-)   
10      68                                     (Rp-, Wk-)   
12      44                                     (Ec+, Rp+)   

                                      HASNO HAS CONTAINS        ISIN  \
node                                                                   
1     (DEAD, hull, must_lock, scc, waiting)  ()       ()  (may_lock)   
10               (INIT, hull, scc, waiting)  ()   (DEAD)  (may_lock)   
12                  (DEAD, INIT, must_lock)  ()    (scc)  (may_lock)   

               EQUALS                  class  
node                                          
1              (INIT)             (may_lock)  
10        (must_lock)  (may_lock, must_lock)  
12    (hull, waiting)    (may_lock, waiting)

The resulting graph has three components, they are all in class `may_lock`, one is in class `must_lock`, and one in class `waiting`. More options are available to `classify()`, in particular:

 - `_limit=256` to limit the size of the resulting graph
 - `_split=True` that can be set to `False` to reuse existing components instead of splitting them
 - `_src` and `_dst` can be used to add the class of source and destination nodes in the edges table

Moreover, `classify()` can be called on a component graph already split, not necessarily on a graph with a single node that hols all the states as we did here.

## Drawing component graphs

We have noted that some components are decorated with a symbol, here is the complete list of these symbols with their interpretation:

 - ▶ component is exactly the set of initial states
 - ▷ component contains initial states, maybe only some, or all but together with non-initial states
 - ⏺ component is an SCC
 - ☍ component is a SCC convex hull
 - ○ component contains at least one SCC, but is not a SCC itself and neither a hull
 - ⏹ component is exactly the set of deadlocks
 - □ component contains deadlocks, maybe only some, or all but together with non-deadlock states

A component that has none of this symbol simply does not fall in any of the above cases.

As shown above, if a Python cell of the Jupyter Notebook has a component graph as its result, the graph is displayed as an interactive widget. To have more control over the drawing, we can use the method `draw()` which accepts a great number of options. In general, there is a match between the interactive interface and the options to `draw()`, for instance, in tab _Nodes / Fill_ there is an option _color_ that allows to choose the fill color of nodes from the columns of the nodes table. This is matched with an option `nodes_fill_color` that accepts the name of a column as its value, or an array of colors (eg, in HTML hexadecimal format) that will be assigned to the nodes.

Details about the available options are given by the documentation of class `ecco.cygraphs.Graph`, a more didactic documentation may be written in the future, but is out of the scope of state-space analysis.

In [16]:
from ecco.cygraphs import Graph
Graph?

Init signature: Graph(nodes, edges, **args)
Docstring:     
An interactive graph that can be displayed in Jupyter

Arguments:
 - `nodes` (`pandas.DataFrame`): nodes table whose index is called `node`
 - `edges` (`pandas.DataFrame`): edges table whose index has two columns
   called `src` and |dst`

Graph options:
 - `layout` (`str` or `tuple[str,dict]`): a layout algorithm, or a pair
   `(algo, options)` where options are the parameters for the chosen
   algorithm
 - `layout_extra` (`dict`): additional layout algorithms to be added to
   the UI, mapping names to functions or static positions

Most nodes and edges options may be given as a single value that
is applied to every nodes/edges, or as the name of a column in
`nodes`/`edges` containing the values to apply to each node/edge,
or as an array of values whose length is the number of
nodes/edges. When a column or an array is provided, it must
contain valid values for the expected property, except for the
color that can be computed i